<a href="https://colab.research.google.com/github/MoohShadox/Web_Semantique_Workshop/blob/master/Solutions/Exercice%2002%20-%20Data%20Querying%20(SPARQL)%20.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [5]:
!git clone https://github.com/MoohShadox/Web_Semantique_Workshop

fatal: destination path 'Web_Semantique_Workshop' already exists and is not an empty directory.


# Exercice : Data Querying
Le but de cet exercice est de voire comment manipuler une source de données RDF déja existante, cette source est disponible sur GitHub, a travers ça l'objectif recherché est : 
- De mieux manipuler SPARQL
- De voire un cas d'application réel ou RDF a été utilisé pour annoter des données.

A chaque étape le but serra de satisfaire un besoin je vous laisse les sorties attendus mais si vous recliquez ça s'effacera.

Première étape : Créer le graphe a partir du fichier et le charger, vous pouvez afficher le contenu du fichier en utilisant la fonction cat.

In [6]:
!pip install rdflib
import rdflib
graphe  = rdflib.Graph()
!cat /content/Web_Semantique_Workshop/gemet-backbone.rdf | head
graphe.parse("/content/Web_Semantique_Workshop/gemet-backbone.rdf")

<?xml version="1.0" encoding="UTF-8" ?>
<rdf:RDF xmlns:rdf="http://www.w3.org/1999/02/22-rdf-syntax-ns#"
    xmlns:rdfs='http://www.w3.org/2000/01/rdf-schema#'
    xmlns:skos="http://www.w3.org/2004/02/skos/core#"
    xmlns:gemet="http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#"
    xml:base="http://www.eionet.europa.eu/gemet/">

<skos:Collection rdf:about="supergroup/">
    <rdfs:label>GEMET Supergroups</rdfs:label>
    <skos:prefLabel>Supergroups</skos:prefLabel>


<Graph identifier=N449f93c229da4ea7b359f5d91fc8d4f4 (<class 'rdflib.graph.Graph'>)>

Maintenant essayons d'explorer notre fichier donc la première étape serra de voire les concepts qui sont utilisés par l'ontologie.
Ici le but est de générer les noms de toutes les classes du fichier donc de trouver tous les tuples <Sujet, is a, Classe> en utilisant un filtre (pas de requète SPARQL pour l'instant)

In [7]:
for i in graphe.triples((None,rdflib.RDF.term("type"),None)):
    print(i[0],"-",i[2])

http://www.eionet.europa.eu/gemet/theme/31 - http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#Theme
http://www.eionet.europa.eu/gemet/theme/36 - http://www.w3.org/2004/02/skos/core#Collection
http://www.eionet.europa.eu/gemet/group/96 - http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#Group
http://www.eionet.europa.eu/gemet/theme/39 - http://www.w3.org/2004/02/skos/core#Collection
http://www.eionet.europa.eu/gemet/group/3875 - http://www.w3.org/2004/02/skos/core#Collection
http://www.eionet.europa.eu/gemet/group/4750 - http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#Group
http://www.eionet.europa.eu/gemet/group/8603 - http://www.w3.org/2004/02/skos/core#Collection
http://www.eionet.europa.eu/gemet/theme/21 - http://www.w3.org/2004/02/skos/core#Collection
http://www.eionet.europa.eu/gemet/theme/23 - http://www.w3.org/2004/02/skos/core#Collection
http://www.eionet.europa.eu/gemet/theme/29 - http://www.w3.org/2004/02/skos/core#Collection
http://www.eionet.eu

In [0]:
#Essayez d'identifier le namespace le plus utile a concerver 
ont_ns = "https://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#"
#Maintenant on va sérializer le fichier en turtle pour pouvoir le visualiser ce qui va vous aider dans l'écriture des requètes
graphe.serialize("gemet-backbone-turtle.rdf","turtle")

In [9]:
!cat gemet-backbone-turtle.rdf

@prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix skos: <http://www.w3.org/2004/02/skos/core#> .

<http://www.eionet.europa.eu/gemet/group/> a skos:Collection ;
    rdfs:label "GEMET Groups" ;
    skos:inScheme <http://www.eionet.europa.eu/gemet/gemetThesaurus> ;
    skos:member <http://www.eionet.europa.eu/gemet/group/10111>,
        <http://www.eionet.europa.eu/gemet/group/10112>,
        <http://www.eionet.europa.eu/gemet/group/10114>,
        <http://www.eionet.europa.eu/gemet/group/10117>,
        <http://www.eionet.europa.eu/gemet/group/10118>,
        <http://www.eionet.europa.eu/gemet/group/1062>,
        <http://www.eionet.europa.eu/gemet/group/13109>,
        <http://www.eionet.europa.eu/gemet/group/1349>,
        <http://www.eionet.europa.eu/gemet/group/14979>,
        <http://www.eionet.europa.eu/gemet/group/14980>,
        <http://www.eionet.europa.eu/gemet/group/1922>,
        <ht

In [10]:
"""
Pour vous aider je vous donne cet exemple de requètes qui récupérent tous les tuples du graphe rdf (et qui en garde
50) 
Les prefixes que j'ai pris ont été pris en utilisant ceux du fichier turtle.
J'ai aussi codé un affichage que vous pouvez réutiliser pour voire les réponses de vos requètes et que j'utiliserais
dans la solution.
"""

requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
SELECT ?s ?p ?o
WHERE {
?s ?p ?o
}
LIMIT 50
"""
rez = graphe.query(requete)
for i in rez:
    print("===")
    cpt = 0
    for j in i:
        print(cpt," - ",j)
        cpt = cpt + 1
    print("====")

===
0  -  http://www.eionet.europa.eu/gemet/theme/6
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/5976
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/7
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/15096
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/4785
1  -  http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#theme
2  -  http://www.eionet.europa.eu/gemet/theme/34
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/40
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/3106
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/4356
1  -  http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#group
2  -  http://www.eionet.europa.eu/gemet/group/893
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/6406
1  -  http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#group
2  -  http://www.eionet.euro

Pour commencer prenons une classe, par exemple la classe Theme.

Et affichons 100 exemples de cette classe avec tous les tuples qui y sont associés

In [11]:
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
SELECT ?s ?p ?o 
WHERE {
?s rdf:type gemet:Theme .
?s ?p ?o
}
LIMIT 5000
"""
rez = graphe.query(requete)
for i in rez:
    print("===")
    cpt = 0
    for j in i:
        print(cpt," - ",j)
        cpt = cpt + 1
    print("====")

Le flux de sortie a été tronqué et ne contient que les 5000 dernières lignes.
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/121
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/15253
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/3871
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/4284
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/11763
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet

===
0  -  http://www.eionet.europa.eu/gemet/theme/20
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/14873
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/20
1  -  http://www.w3.org/2004/02/skos/core#member
2  -  http://www.eionet.europa.eu/gemet/concept/1988
====

Première question que vous devez vous poser : 
Pourquoi cette requète ne donne aucune donnée littérale (String, int ou autre) ? 
Il suffit de cliquer sur un des liens que la requète renvoie pour comprendre pourquoi.

La réponse est que cette base d'annotations est un exemple ou les URI ne sont pas fictifs, ils référencent vraiment un contenu en ligne que le fichier RDF ne fait qu'annoter en précisant les ressources associées.

In [12]:
"""
Afin de récupérer les titres des pages vers lesquelles pointent les URI je vous donne cette fonction que vous
permettra in-fine d'avoir une idée sur le contenu des pages.
"""
import requests
import re
def get_content(uri):
    r = requests.get(uri)
    text = str(r.content)
    L = re.findall("<title>(.*?)</title>",text)
    LL = []
    for i in L:
        LL.append(i.replace("\\n","").strip())
    return LL[0]

get_content("http://www.eionet.europa.eu/gemet/theme/20")

'information'

In [13]:
"""
Maintenant on va extraire une partie des themes et tous les membres qui leurs sont reliés, on va les mettre dans un
graphe qu'on va enrichir au fur et a mesure.
"""
mon_ns = "https://monns/ontologie#"
skos_ns = "http://www.w3.org/2004/02/skos/core#"

graphe2 = rdflib.Graph()

requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
SELECT ?s ?m
WHERE {
?s rdf:type gemet:Theme .
?s skos:member ?m .
}
LIMIT 5000
"""
rez = graphe.query(requete)
for i in rez:
    print("===")
    cpt = 0
    for j in i:
        print(cpt," - ",j)
        cpt = cpt + 1
    graphe2.add((i[0],rdflib.RDF.term("type"),rdflib.URIRef(skos_ns+"theme")))
    graphe2.add((i[1],rdflib.RDF.term("type"),rdflib.URIRef(skos_ns+"concept")))
    graphe2.add((i[0],rdflib.URIRef(skos_ns+"member"),i[1]))
    print("====")

Le flux de sortie a été tronqué et ne contient que les 5000 dernières lignes.
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/5752
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/6064
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/173
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/360
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/1350
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/7126
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/10106
====
===
0  -  http://www.eionet.europa.eu/gemet/theme/17
1  -  http://www.eionet.europa.eu/gemet/concept/5144
====
===
0  -  http://www.eionet.europa.eu/g

In [14]:
graphe2.serialize("graphe_2.rdf","turtle")
!cat graphe_2.rdf

@prefix ns1: <http://www.w3.org/2004/02/skos/core#> .

<http://www.eionet.europa.eu/gemet/theme/1> a ns1:theme ;
    ns1:member <http://www.eionet.europa.eu/gemet/concept/100>,
        <http://www.eionet.europa.eu/gemet/concept/10012>,
        <http://www.eionet.europa.eu/gemet/concept/10067>,
        <http://www.eionet.europa.eu/gemet/concept/103>,
        <http://www.eionet.europa.eu/gemet/concept/105>,
        <http://www.eionet.europa.eu/gemet/concept/107>,
        <http://www.eionet.europa.eu/gemet/concept/1075>,
        <http://www.eionet.europa.eu/gemet/concept/108>,
        <http://www.eionet.europa.eu/gemet/concept/10833>,
        <http://www.eionet.europa.eu/gemet/concept/10980>,
        <http://www.eionet.europa.eu/gemet/concept/10981>,
        <http://www.eionet.europa.eu/gemet/concept/10985>,
        <http://www.eionet.europa.eu/gemet/concept/10986>,
        <http://www.eionet.europa.eu/gemet/concept/10988>,
        <http://www.eionet.europa.eu/gemet/concept/10992>,
      

In [16]:
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
SELECT ?s 
WHERE {
?s rdf:type skos:theme .
}
"""
rez = graphe2.query(requete)
L = list(rez)
cpt = 1
for i in L:
    print("===")
    for j in i:
        print(cpt,"/",len(L)," - ",j)
    cpt = cpt + 1
    graphe2.add((i[0],rdflib.URIRef(mon_ns+"contenu"),rdflib.Literal(get_content(i[0]))))
    print("====")

===
1 / 24  -  http://www.eionet.europa.eu/gemet/theme/17
====
===
2 / 24  -  http://www.eionet.europa.eu/gemet/theme/18
====
===
3 / 24  -  http://www.eionet.europa.eu/gemet/theme/23
====
===
4 / 24  -  http://www.eionet.europa.eu/gemet/theme/38
====
===
5 / 24  -  http://www.eionet.europa.eu/gemet/theme/20
====
===
6 / 24  -  http://www.eionet.europa.eu/gemet/theme/21
====
===
7 / 24  -  http://www.eionet.europa.eu/gemet/theme/1
====
===
8 / 24  -  http://www.eionet.europa.eu/gemet/theme/13
====
===
9 / 24  -  http://www.eionet.europa.eu/gemet/theme/19
====
===
10 / 24  -  http://www.eionet.europa.eu/gemet/theme/29
====
===
11 / 24  -  http://www.eionet.europa.eu/gemet/theme/15
====
===
12 / 24  -  http://www.eionet.europa.eu/gemet/theme/14
====
===
13 / 24  -  http://www.eionet.europa.eu/gemet/theme/39
====
===
14 / 24  -  http://www.eionet.europa.eu/gemet/theme/2
====
===
15 / 24  -  http://www.eionet.europa.eu/gemet/theme/12
====
===
16 / 24  -  http://www.eionet.europa.eu/gemet/t

In [17]:
graphe2.serialize("graphe_2.rdf","turtle")
!cat graphe_2.rdf

@prefix ns1: <http://www.w3.org/2004/02/skos/core#> .
@prefix ns2: <https://monns/ontologie#> .

<http://www.eionet.europa.eu/gemet/theme/1> a ns1:theme ;
    ns1:member <http://www.eionet.europa.eu/gemet/concept/100>,
        <http://www.eionet.europa.eu/gemet/concept/10012>,
        <http://www.eionet.europa.eu/gemet/concept/10067>,
        <http://www.eionet.europa.eu/gemet/concept/103>,
        <http://www.eionet.europa.eu/gemet/concept/105>,
        <http://www.eionet.europa.eu/gemet/concept/107>,
        <http://www.eionet.europa.eu/gemet/concept/1075>,
        <http://www.eionet.europa.eu/gemet/concept/108>,
        <http://www.eionet.europa.eu/gemet/concept/10833>,
        <http://www.eionet.europa.eu/gemet/concept/10980>,
        <http://www.eionet.europa.eu/gemet/concept/10981>,
        <http://www.eionet.europa.eu/gemet/concept/10985>,
        <http://www.eionet.europa.eu/gemet/concept/10986>,
        <http://www.eionet.europa.eu/gemet/concept/10988>,
        <http://www.eio

In [18]:
#Maintenons voyons les contenus qu'on a extrait
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
prefix ns2: <https://monns/ontologie#> 
SELECT ?s ?c
WHERE {
?s ns2:contenu ?c .
}
"""
rez = graphe2.query(requete)
L = list(rez)
cpt = 1
for i in L:
    print("===")
    for j in i:
        print(cpt,"/",len(L)," - ",j)
    cpt = cpt + 1
    graphe2.add((i[0],rdflib.URIRef(mon_ns+"contenu"),rdflib.Literal(i[1])))
    print("====")

===
1 / 24  -  http://www.eionet.europa.eu/gemet/theme/36
1 / 24  -  space
====
===
2 / 24  -  http://www.eionet.europa.eu/gemet/theme/21
2 / 24  -  legislation
====
===
3 / 24  -  http://www.eionet.europa.eu/gemet/theme/23
3 / 24  -  natural areas, landscape, ecosystems
====
===
4 / 24  -  http://www.eionet.europa.eu/gemet/theme/13
4 / 24  -  food, drinking water
====
===
5 / 24  -  http://www.eionet.europa.eu/gemet/theme/3
5 / 24  -  air
====
===
6 / 24  -  http://www.eionet.europa.eu/gemet/theme/12
6 / 24  -  fishery
====
===
7 / 24  -  http://www.eionet.europa.eu/gemet/theme/39
7 / 24  -  waste
====
===
8 / 24  -  http://www.eionet.europa.eu/gemet/theme/7
8 / 24  -  climate
====
===
9 / 24  -  http://www.eionet.europa.eu/gemet/theme/17
9 / 24  -  human health
====
===
10 / 24  -  http://www.eionet.europa.eu/gemet/theme/25
10 / 24  -  physics
====
===
11 / 24  -  http://www.eionet.europa.eu/gemet/theme/16
11 / 24  -  geography
====
===
12 / 24  -  http://www.eionet.europa.eu/gemet/t

In [0]:
# A vous de faire la même chose pour les concepts qu'on trouve dans la base de données

In [20]:
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
SELECT ?s 
WHERE {
?s rdf:type skos:concept .
}
"""
rez = graphe2.query(requete)
L = list(rez)
cpt = 1
limite = 30
for i in L:
    print("===")
    for j in i:
        print(cpt,"/",len(L)," - ",j)
    cpt = cpt + 1
    if(cpt == limite):
        break
    graphe2.add((i[0],rdflib.URIRef(mon_ns+"contenu"),rdflib.Literal(get_content(i[0]))))
    print("====")

===
1 / 3662  -  http://www.eionet.europa.eu/gemet/concept/10084
====
===
2 / 3662  -  http://www.eionet.europa.eu/gemet/concept/661
====
===
3 / 3662  -  http://www.eionet.europa.eu/gemet/concept/8573
====
===
4 / 3662  -  http://www.eionet.europa.eu/gemet/concept/100
====
===
5 / 3662  -  http://www.eionet.europa.eu/gemet/concept/4691
====
===
6 / 3662  -  http://www.eionet.europa.eu/gemet/concept/12011
====
===
7 / 3662  -  http://www.eionet.europa.eu/gemet/concept/25
====
===
8 / 3662  -  http://www.eionet.europa.eu/gemet/concept/2767
====
===
9 / 3662  -  http://www.eionet.europa.eu/gemet/concept/627
====
===
10 / 3662  -  http://www.eionet.europa.eu/gemet/concept/6859
====
===
11 / 3662  -  http://www.eionet.europa.eu/gemet/concept/6387
====
===
12 / 3662  -  http://www.eionet.europa.eu/gemet/concept/5282
====
===
13 / 3662  -  http://www.eionet.europa.eu/gemet/concept/8931
====
===
14 / 3662  -  http://www.eionet.europa.eu/gemet/concept/15205
====
===
15 / 3662  -  http://www.ei

In [21]:
#Maintenons voyons les contenus qu'on a extrait
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
prefix ns2: <https://monns/ontologie#> 
SELECT ?s ?t ?c
WHERE {
?s ns2:contenu ?c .
?s rdf:type ?t
}
"""
rez = graphe2.query(requete)
for i in rez:
    print("===")
    cpt = 0
    for j in i:
        print(cpt," - ",j)
        cpt = cpt + 1
    print("====")

===
0  -  http://www.eionet.europa.eu/gemet/concept/10084
1  -  http://www.w3.org/2004/02/skos/core#concept
2  -  law branch
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/661
1  -  http://www.w3.org/2004/02/skos/core#concept
2  -  authority body
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/8573
1  -  http://www.w3.org/2004/02/skos/core#concept
2  -  trade relations
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/4691
1  -  http://www.w3.org/2004/02/skos/core#concept
2  -  large combustion plant
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/100
1  -  http://www.w3.org/2004/02/skos/core#concept
2  -  administrative body
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/12011
1  -  http://www.w3.org/2004/02/skos/core#concept
2  -  biofuel
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/25
1  -  http://www.w3.org/2004/02/skos/core#concept
2  -  accident
====
===
0  -  http://www.eionet.europa.eu/gemet/concept/2767
1  -  http://www.

In [22]:
#Maintenant l'objectif est de construire un dictionnaire theme : concepts réliés 
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
prefix ns2: <https://monns/ontologie#> 
SELECT ?cs ?cm
WHERE {
?s rdf:type skos:theme .
?s skos:member ?m .
?s ns2:contenu ?cs .
?m ns2:contenu ?cm .
}
"""
D = {}
rez = graphe2.query(requete)
for i in rez:
    print("===")
    cpt = 0
    for j in i:
        print(cpt," - ",j)
        cpt = cpt + 1
    D[str(i[0])] = D.get(str(i[0]),[]) + [str(i[1])]
    print("====")

===
0  -  human health
1  -  accident
====
===
0  -  human health
1  -  respiratory tract
====
===
0  -  human health
1  -  animal disease
====
===
0  -  human health
1  -  oncology
====
===
0  -  natural areas, landscape, ecosystems
1  -  ice sheet
====
===
0  -  legislation
1  -  law branch
====
===
0  -  legislation
1  -  regulation
====
===
0  -  legislation
1  -  vehicle inspection
====
===
0  -  legislation
1  -  public waterways domain
====
===
0  -  administration
1  -  trade relations
====
===
0  -  administration
1  -  minimal cost planning
====
===
0  -  administration
1  -  authority body
====
===
0  -  administration
1  -  administrative body
====
===
0  -  administration
1  -  political party
====
===
0  -  industry
1  -  large combustion plant
====
===
0  -  industry
1  -  waste processing industry
====
===
0  -  industry
1  -  firing
====
===
0  -  industry
1  -  quality assurance
====
===
0  -  general
1  -  quality assurance
====
===
0  -  forestry
1  -  ice sheet
===

In [23]:
import json
#On formatte tout ça en Json et on tri selon les clefs
print(json.dumps(D, sort_keys=True, indent=4))

{
    "administration": [
        "trade relations",
        "minimal cost planning",
        "authority body",
        "administrative body",
        "political party"
    ],
    "agriculture": [
        "biofuel",
        "agrochemical"
    ],
    "air": [
        "atmospheric layering",
        "firing"
    ],
    "climate": [
        "atmospheric layering"
    ],
    "environmental policy": [
        "environmental accounting",
        "ice sheet"
    ],
    "fishery": [
        "drift net fishing",
        "fishery economics"
    ],
    "forestry": [
        "ice sheet"
    ],
    "general": [
        "quality assurance"
    ],
    "human health": [
        "accident",
        "respiratory tract",
        "animal disease",
        "oncology"
    ],
    "industry": [
        "large combustion plant",
        "waste processing industry",
        "firing",
        "quality assurance"
    ],
    "legislation": [
        "law branch",
        "regulation",
        "vehicle inspection",

In [25]:
"""Maintenant imaginez qu'on veuille limiter notre recherche d'URI couteuse en mémoire aux 10 thémes
qui ont le plus de concepts
 - Revoyez comment on fait une aggrégation avec GroupBy
 - Checkez la documentation officielle pour voire des exemples en Sparql
et essayez d'écrire la requète qui fait ça.
"""
top = "10"
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
SELECT ?s (count(?m) as ?nb_m)
WHERE {
    ?s rdf:type gemet:Theme .
    ?s skos:member ?m .
}
GROUP BY ?s
ORDER BY DESC(?nb_m)
LIMIT %t
""".replace("%t",top)

rez = graphe.query(requete)
cpt = 1
D = {}
D["Theme"] = []
D["Classement"] = []
D["Nombre de termes"] = []

for i in rez:
    c=get_content(i[0])
    print("-",end="")
    D["Theme"].append(c)
    D["Classement"].append(cpt)
    D["Nombre de termes"].append(int(i[1]))
    cpt = cpt + 1
    
print("")
print("==TOP {}==".format(str(top)))
import pandas as pd
df = pd.DataFrame(D)
print(df)
print("=========")

print("==TOP {} STATS==".format(str(top)))
print(df.describe()["Nombre de termes"])
print("=========")

----------
==TOP 10==
                                  Theme  Classement  Nombre de termes
0                               biology           1               691
1                             chemistry           2               601
2                             pollution           3               576
3                                 water           4               569
4                              industry           5               567
5                             economics           6               501
6                  environmental policy           7               492
7            social aspects, population           8               483
8  natural areas, landscape, ecosystems           9               466
9                              research          10               430
==TOP 10 STATS==
count     10.000000
mean     537.600000
std       77.445608
min      430.000000
25%      485.250000
50%      534.000000
75%      574.250000
max      691.000000
Name: Nombre de termes, dtype: 

**Bonus : le mot clef CONSTRUCT**
Ce mot clef permet d'utiliser les variables extraite pour construire un autre graphe.
Par exemple ici on construit un graphe qui ne lie que des litéraux (juste pour l'exemple) 

In [26]:
requete = """
prefix gemet: <http://www.eionet.europa.eu/gemet/2004/06/gemet-schema.rdf#> 
prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> 
prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> 
prefix skos: <http://www.w3.org/2004/02/skos/core#> 
prefix xml: <http://www.w3.org/XML/1998/namespace> 
prefix xsd: <http://www.w3.org/2001/XMLSchema#> 
prefix ns2: <https://monns/ontologie#> 
CONSTRUCT {?cs ns2:inLexiqueOf ?cm}
WHERE {
?s rdf:type skos:theme .
?s skos:member ?m .
?s ns2:contenu ?cs .
?m ns2:contenu ?cm .
}
"""

D = {}
rez = graphe2.query(requete)
for i in rez:
    print(i)

(rdflib.term.Literal('administration'), rdflib.term.URIRef('https://monns/ontologie#inLexiqueOf'), rdflib.term.Literal('trade relations'))
(rdflib.term.Literal('administration'), rdflib.term.URIRef('https://monns/ontologie#inLexiqueOf'), rdflib.term.Literal('minimal cost planning'))
(rdflib.term.Literal('fishery'), rdflib.term.URIRef('https://monns/ontologie#inLexiqueOf'), rdflib.term.Literal('fishery economics'))
(rdflib.term.Literal('fishery'), rdflib.term.URIRef('https://monns/ontologie#inLexiqueOf'), rdflib.term.Literal('drift net fishing'))
(rdflib.term.Literal('air'), rdflib.term.URIRef('https://monns/ontologie#inLexiqueOf'), rdflib.term.Literal('firing'))
(rdflib.term.Literal('trade, services'), rdflib.term.URIRef('https://monns/ontologie#inLexiqueOf'), rdflib.term.Literal('trade relations'))
(rdflib.term.Literal('agriculture'), rdflib.term.URIRef('https://monns/ontologie#inLexiqueOf'), rdflib.term.Literal('biofuel'))
(rdflib.term.Literal('environmental policy'), rdflib.term.URI

In [27]:
import networkx as nx

G=nx.Graph()
names = {}
nodes = []
edges = []
for i in list(rez):
  G.add_node(str(i[0]))
  G.add_node(str(i[2]))
  names[str(i[0])] = str(i[0])
  names[str(i[2])] = str(i[2])
  edge = (str(i[0]),str(i[2]))
  nodes.append(str(i[0]))
  nodes.append(str(i[2]))

  edges.append(edge)
  G.add_edge(*edge)

H=nx.relabel_nodes(G,names)
print(names)

print("Nodes of graph: ")
print(G.nodes())
print("Edges of graph: ")
print(G.edges())

{'administration': 'administration', 'trade relations': 'trade relations', 'minimal cost planning': 'minimal cost planning', 'fishery': 'fishery', 'fishery economics': 'fishery economics', 'drift net fishing': 'drift net fishing', 'air': 'air', 'firing': 'firing', 'trade, services': 'trade, services', 'agriculture': 'agriculture', 'biofuel': 'biofuel', 'environmental policy': 'environmental policy', 'environmental accounting': 'environmental accounting', 'legislation': 'legislation', 'public waterways domain': 'public waterways domain', 'vehicle inspection': 'vehicle inspection', 'general': 'general', 'quality assurance': 'quality assurance', 'human health': 'human health', 'animal disease': 'animal disease', 'political party': 'political party', 'authority body': 'authority body', 'administrative body': 'administrative body', 'soil': 'soil', 'nutrient content': 'nutrient content', 'respiratory tract': 'respiratory tract', 'law branch': 'law branch', 'industry': 'industry', 'waste proc

In [29]:
nodes = set()
for i in edges:
  nodes.add(i[0])
  nodes.add(i[1])
nodes=list(nodes)
print(nodes)
e = []
for i in edges:
  e.append(
      (
          nodes.index(i[0]),
          nodes.index(i[1])
      )
  )
edges = e
print(edges)

['air', 'waste processing industry', 'administration', 'public waterways domain', 'bitumen', 'waste', 'general', 'quality assurance', 'animal disease', 'drift net fishing', 'human health', 'climate', 'industry', 'agrochemical', 'fossil fuel consumption', 'trade relations', 'atmospheric layering', 'soil', 'environmental accounting', 'non-energy use', 'forestry', 'regulation', 'fishery economics', 'fishery', 'minimal cost planning', 'natural areas, landscape, ecosystems', 'trade, services', 'agriculture', 'environmental policy', 'nutrient content', 'political party', 'law branch', 'ice sheet', 'vehicle inspection', 'large combustion plant', 'respiratory tract', 'firing', 'biofuel', 'authority body', 'legislation', 'resources', 'accident', 'oncology', 'physics', 'administrative body']
[(2, 15), (2, 24), (23, 22), (23, 9), (0, 36), (26, 15), (27, 37), (28, 18), (39, 3), (39, 33), (6, 7), (10, 8), (2, 30), (2, 38), (2, 44), (17, 29), (10, 35), (39, 31), (12, 1), (11, 16), (0, 16), (40, 14),

In [30]:
#Maintenant on fait un petit display plus interactif et plus esthétique
import plotly.graph_objects as go

import networkx as nx

G = nx.random_geometric_graph(len(nodes), 0.5)

edge_x = []
edge_y = []
for edge in edges:
    x0, y0 = G.nodes[edge[0]]['pos']
    x1, y1 = G.nodes[edge[1]]['pos']
    edge_x.append(x0)
    edge_x.append(x1)
    edge_x.append(None)
    edge_y.append(y0)
    edge_y.append(y1)
    edge_y.append(None)

edge_trace = go.Scatter(
    x=edge_x, y=edge_y,
    line=dict(width=0.5, color='#888'),
    hoverinfo='none',
    mode='lines')

node_x = []
node_y = []
for node in range(0,len(nodes)):
    x, y = G.nodes[node]['pos']
    node_x.append(x)
    node_y.append(y)

node_trace = go.Scatter(
    x=node_x, y=node_y,
    mode='markers',
    hoverinfo='text',
    marker=dict(
        showscale=True,
        # colorscale options
        #'Greys' | 'YlGnBu' | 'Greens' | 'YlOrRd' | 'Bluered' | 'RdBu' |
        #'Reds' | 'Blues' | 'Picnic' | 'Rainbow' | 'Portland' | 'Jet' |
        #'Hot' | 'Blackbody' | 'Earth' | 'Electric' | 'Viridis' |
        colorscale='YlGnBu',
        reversescale=True,
        color=[],
        size=10,
        colorbar=dict(
            thickness=15,
            title='Node Connections',
            xanchor='left',
            titleside='right'
        ),
        line_width=2))

node_adjacencies = []
node_text = []
for node, adjacencies in enumerate(G.adjacency()):
    node_adjacencies.append(len(adjacencies[1]))
    node_text.append(nodes[node])

node_trace.marker.color = node_adjacencies
node_trace.text = node_text


fig = go.Figure(data=[edge_trace, node_trace],
             layout=go.Layout(
                title='<br>Network graph made with Python',
                titlefont_size=16,
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20,l=5,r=5,t=40),
                annotations=[ dict(
                    text="Python code: <a href='https://plotly.com/ipython-notebooks/network-graphs/'> https://plotly.com/ipython-notebooks/network-graphs/</a>",
                    showarrow=False,
                    xref="paper", yref="paper",
                    x=0.005, y=-0.002 ) ],
                xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                )
fig.show()